In [76]:
from music21 import *
import numpy as np
from keras.utils.np_utils import to_categorical
environment.set('autoDownload', 'allow')
from keras.models import Sequential
from keras.layers import Dense, Dropout, Embedding, LSTM, Activation
import pickle

In [2]:
file = 'C:/Users/kevin/ML/Music Generation/Charlie Puth - Done For Me.mid'
score = converter.parse(file)

In [3]:
notes_to_parse = None
notes = []
parts = instrument.partitionByInstrument(score)
if parts: # file has instrument parts
    notes_to_parse = parts.parts[0].recurse()
else: # file has notes in a flat structure
    notes_to_parse = score.flat.notes
for element in notes_to_parse:
    if isinstance(element, note.Note):
        notes.append(str(element.pitch))
    elif isinstance(element, chord.Chord):
        notes.append('.'.join(str(n) for n in element.normalOrder))

In [4]:
seq_length = 100

pitchnames = sorted(set(item for item in notes))
note_to_int = dict((note, number) for number, note in enumerate(pitchnames))

In [15]:
notes[100]

'D4'

In [13]:
test_in = []
test_out = []
for i in range(0, len(notes) - seq_length, 1):
    test_in = notes[i:i + seq_length]
    test_out = notes[i + seq_length]
    print ("test_in at %i = %s" %(i, str(test_in)))
    print ("test_in at %i = %s" %(i, str(test_out)))

test_in at 0 = ['F#4', 'B1', '9.10', 'A4', 'B4', 'D5', '9.10', '9.10', 'A3', 'A3', 'B4', '9.10', 'B3', 'D4', 'B-3', 'B-3', 'B3', 'A3', 'D4', '9.10', 'A3', '9.2', 'B-3', 'D4', 'B2', 'B1', 'B3', 'B3', '2.6', 'D5', '6.7.8.9', 'F#4', 'B4', 'G#1', 'G#3', 'D4', 'B3', 'D4', 'B4', 'G#1', 'B3', 'D5', 'G#1', 'B3', 'B3', 'D4', 'B3', 'G#1', 'B3', 'D4', 'G#1', '5.6.7.10', '5.6.10', 'F#4', '9.11', '6.11', 'G1', 'D4', '2.4', '4.9', '9.10', '9.11', 'A3', 'B3', 'B3', 'D4', '7.11', 'G1', 'B3', 'B3', 'A3', '9.10', '9.2', 'A3', 'A3', 'B3', 'D4', 'B3', '7.10', 'G1', 'G1', 'G1', 'D4', '0.5.6', 'E5', 'E4', '11.0.1.6', 'B3', 'C#2', 'F#5', 'F#4', 'E4', 'E4', 'F#4', '10.2.4', '1.2', 'F#5', 'E5', '1.4.5.6.7', 'B-3']
test_in at 0 = D4
test_in at 1 = ['B1', '9.10', 'A4', 'B4', 'D5', '9.10', '9.10', 'A3', 'A3', 'B4', '9.10', 'B3', 'D4', 'B-3', 'B-3', 'B3', 'A3', 'D4', '9.10', 'A3', '9.2', 'B-3', 'D4', 'B2', 'B1', 'B3', 'B3', '2.6', 'D5', '6.7.8.9', 'F#4', 'B4', 'G#1', 'G#3', 'D4', 'B3', 'D4', 'B4', 'G#1', 'B3', 'D5

test_in at 1359 = ['F#4', 'F7', 'B-3', '8.10', 'D5', 'F#1', 'F#7', 'E5', 'F#1', 'C#7', 'E-7', '4.7', '5.9.10', '4.8', '0.1.2.4.5.6.7', 'B6', 'B4', '6.10', 'D4', '2.6.10', '4.5', '2.3', 'D7', '3.4.5', 'C#7', '8.9.10.3', '4.7', '2.6.9.10', '11.0.1.2.3.4.5.6.7.8.9', '9.10.11.0.2', '10.11.0', 'F7', '5.7.8.10.11', '3.4.5.10', 'C#6', 'C#5', '7.9.10.1', '8.10.0.1', 'F#4', '8.9', '5.9.10', 'G#6', '8.11', 'B-3', '2.5.7', '6.10.11', 'G1', 'G#1', '9.0', '5.6.11', '2.4.5.6.7.8.9.10.11', '0.3.6.8', '6.8.9.10', '2.3.4.6.7.8.10', '10.11.3.5', '5.9.11', '9.10', '2.4', '2.3.7.9.10', '6.9', 'C#5', '9.10.2', '8.1', '9.0.2.4.5.6', '6.7.9.11', '7.8.11', 'F#4', 'D5', '10.11', '9.10.11', 'B-1', '9.11', 'B-3', 'A4', 'B2', 'B-3', 'B4', '5.10.11', '6.7.10.0.2.3', '11.1.2.5', '10.0', '11.1.2.4', 'F#4', 'D4', 'B-1', '4.5.10.11', 'B4', 'F#6', 'B2', 'C#5', '9.11.2.3', '0.1.3.5', '7.8.10.0.3.4', '5.7.8.9.10.0', '2.3.4.5.6.8.9.10', '11.3.4', '10.11.2', 'F#4', 'B1', '4.9']
test_in at 1359 = B-2
test_in at 1360 = ['F7'

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [45]:
network_input = []
network_output = []
# create input sequences and the corresponding outputs
for i in range(0, len(notes) - seq_length, 1):
    sequence_in = notes[i:i + seq_length]
    sequence_out = notes[i + seq_length]
    network_input.append([note_to_int[char] for char in sequence_in])
    network_output.append(note_to_int[sequence_out])

In [46]:
network_input

[[1628,
  1588,
  1485,
  1577,
  1591,
  1610,
  1485,
  1485,
  1576,
  1576,
  1591,
  1485,
  1590,
  1609,
  1583,
  1583,
  1590,
  1576,
  1609,
  1485,
  1576,
  1572,
  1583,
  1609,
  1589,
  1588,
  1590,
  1590,
  647,
  1610,
  1142,
  1628,
  1591,
  1639,
  1641,
  1609,
  1590,
  1609,
  1591,
  1639,
  1590,
  1610,
  1639,
  1590,
  1590,
  1609,
  1590,
  1639,
  1590,
  1609,
  1639,
  972,
  964,
  1628,
  1544,
  1114,
  1645,
  1609,
  594,
  957,
  1485,
  1544,
  1576,
  1590,
  1590,
  1609,
  1225,
  1645,
  1590,
  1590,
  1576,
  1485,
  1572,
  1576,
  1576,
  1590,
  1609,
  1590,
  1207,
  1645,
  1645,
  1645,
  1609,
  162,
  1622,
  1621,
  435,
  1590,
  1595,
  1629,
  1628,
  1621,
  1621,
  1628,
  404,
  165,
  1629,
  1622,
  268,
  1583],
 [1588,
  1485,
  1577,
  1591,
  1610,
  1485,
  1485,
  1576,
  1576,
  1591,
  1485,
  1590,
  1609,
  1583,
  1583,
  1590,
  1576,
  1609,
  1485,
  1576,
  1572,
  1583,
  1609,
  1589,
  1588,
  1590,
 

In [47]:
num_inputs = len(network_input)
n_vocab = len(set(notes))
num_inputs

8178

In [53]:
n_vocab

1652

In [48]:
# reshape the input into a format compatible with LSTM layers
network_input = np.reshape(network_input, (num_inputs, seq_length, 1))

In [49]:
network_input

array([[[1628],
        [1588],
        [1485],
        ...,
        [1622],
        [ 268],
        [1583]],

       [[1588],
        [1485],
        [1577],
        ...,
        [ 268],
        [1583],
        [1609]],

       [[1485],
        [1577],
        [1591],
        ...,
        [1583],
        [1609],
        [1625]],

       ...,

       [[1544],
        [1123],
        [ 334],
        ...,
        [1591],
        [1591],
        [1591]],

       [[1123],
        [ 334],
        [ 595],
        ...,
        [1591],
        [1591],
        [1591]],

       [[ 334],
        [ 595],
        [1009],
        ...,
        [1591],
        [1591],
        [1591]]])

In [50]:
network_input.shape

(8178, 100, 1)

In [51]:
# normalize input
network_input = network_input / float(n_vocab)
network_output = to_categorical(network_output)

In [52]:
network_input

array([[[0.98547215],
        [0.96125908],
        [0.89891041],
        ...,
        [0.98184019],
        [0.1622276 ],
        [0.95823245]],

       [[0.96125908],
        [0.89891041],
        [0.95460048],
        ...,
        [0.1622276 ],
        [0.95823245],
        [0.97397094]],

       [[0.89891041],
        [0.95460048],
        [0.96307506],
        ...,
        [0.95823245],
        [0.97397094],
        [0.98365617]],

       ...,

       [[0.9346247 ],
        [0.67978208],
        [0.20217918],
        ...,
        [0.96307506],
        [0.96307506],
        [0.96307506]],

       [[0.67978208],
        [0.20217918],
        [0.36016949],
        ...,
        [0.96307506],
        [0.96307506],
        [0.96307506]],

       [[0.20217918],
        [0.36016949],
        [0.61077482],
        ...,
        [0.96307506],
        [0.96307506],
        [0.96307506]]])

In [40]:
network_input.shape

(8178, 100, 1)

In [44]:
network_output.shape

(8178, 1652)

In [73]:
## TEST OUT ADDING AN EMBEDDING LAYER WITH MUSIC ##
model = Sequential()
model.add(LSTM(256, input_shape=(network_input.shape[1], network_input.shape[2]), return_sequences=True))
model.add(Dropout(0.3))
model.add(LSTM(512, return_sequences=True))
model.add(Dropout(0.3))
model.add(LSTM(256, return_sequences=False))
model.add(Dense(256))
model.add(Dropout(0.3))
model.add(Dense(n_vocab))
model.add(Activation('softmax'))
model.compile(loss='categorical_crossentropy', optimizer='rmsprop')

In [74]:
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_16 (LSTM)               (None, 100, 256)          264192    
_________________________________________________________________
dropout_11 (Dropout)         (None, 100, 256)          0         
_________________________________________________________________
lstm_17 (LSTM)               (None, 100, 512)          1574912   
_________________________________________________________________
dropout_12 (Dropout)         (None, 100, 512)          0         
_________________________________________________________________
lstm_18 (LSTM)               (None, 256)               787456    
_________________________________________________________________
dense_5 (Dense)              (None, 256)               65792     
_________________________________________________________________
dropout_13 (Dropout)         (None, 256)               0         
__________

In [78]:
import time
start = time.time()
model.fit(network_input, network_output, epochs=200, batch_size=64)
end = time.time()
print ("Took %f seconds" %(end-start))

Epoch 1/200
8178/8178 [==============================] - 56s 7ms/step - loss: 6.3620
Epoch 2/200
8178/8178 [==============================] - 54s 7ms/step - loss: 6.3335
Epoch 3/200
8178/8178 [==============================] - 55s 7ms/step - loss: 6.3209
Epoch 4/200
8178/8178 [==============================] - 57s 7ms/step - loss: 6.3130
Epoch 5/200
8178/8178 [==============================] - 55s 7ms/step - loss: 6.3044
Epoch 6/200
8178/8178 [==============================] - 54s 7ms/step - loss: 6.2962
Epoch 7/200
8178/8178 [==============================] - 54s 7ms/step - loss: 6.2925
Epoch 8/200
8178/8178 [==============================] - 55s 7ms/step - loss: 6.2860
Epoch 9/200
8178/8178 [==============================] - 54s 7ms/step - loss: 6.2836
Epoch 10/200
8178/8178 [==============================] - 54s 7ms/step - loss: 6.2778
Epoch 11/200
8178/8178 [==============================] - 54s 7ms/step - loss: 6.2777
Epoch 12/200
8178/8178 [==============================] - 55s 7

8178/8178 [==============================] - 52s 6ms/step - loss: 6.2698
Epoch 97/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.2706
Epoch 98/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.2698
Epoch 99/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.2686
Epoch 100/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.2684
Epoch 101/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.2697
Epoch 102/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.2680
Epoch 103/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.2685
Epoch 104/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.2710
Epoch 105/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.2694
Epoch 106/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.2691
Epoch 107/200
8178/8178 [==============================] - 5

8178/8178 [==============================] - 52s 6ms/step - loss: 6.8491
Epoch 191/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.8560
Epoch 192/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.8623
Epoch 193/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.8607
Epoch 194/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.8600
Epoch 195/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.8662
Epoch 196/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.8623
Epoch 197/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.8731
Epoch 198/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.8701
Epoch 199/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.8694
Epoch 200/200
8178/8178 [==============================] - 52s 6ms/step - loss: 6.8744
Took 10407.121561 seconds


In [80]:
# save the model to disk
filename = "LSTM_Music_v1.sav"
model.save(filename)